# Using the Emulator with Prospector

In [1]:
import sys, os
sys.path.append(os.path.join(os.getcwd(), '..', 'src'))

import numpy as np

from prospect.fitting import fit_model
from prospect.io.write_results import write_hdf5
from prospect.plotting.utils import sample_posterior

import corner

# Load code from this repository
from utils import *
from obs import *
from models import *
from sps import *

In [2]:
parnames = [
    "logmass",
    "logzsol",
    "logsfr_ratio_1",
    "logsfr_ratio_1",
    "logsfr_ratio_1",
    "logsfr_ratio_1",
    "logsfr_ratio_1",
    "logsfr_ratio_1",
    "dust2",
    "dust_index",
    "dust1_fraction",
    "log_fagn",
    "log_agn_tau",
    "gas_logz",
    "duste_qpah",
    "duste_umin",
    "log_duste_gamma",
]

## Fitting with Emulator

The first thing we need to do is set up the configuration settings, which get passed to the various `load_obs`, `load_sps`, `load_model`, and `fit_model` functions. The settings listed below will work for both the emulator and FSPS fits below. If you'd like to try fitting different mock objects, feel free to change `objid` (you can select any value between `1` and `10_000`).

In [3]:
run_params = {
    # object selection
    'objid': 1,
    # emulator selection
    'emulfp': os.path.join(os.getcwd(), '..', 'data', 'parrot_v4_obsphot_256n_5l_05z30.npy'),
    # dynesty params
    'nested_maxbatch': 0, # maximum number of dynamic patches
    'nested_bound': 'multi', # bounding method
    'nested_sample': 'rwalk', # sampling method
    'nested_walks': 50, # MC walks
    'nested_nlive_batch': 200, # size of live point "batches"
    'nested_nlive_init': 100, # number of initial live points
    'nested_weight_kwargs': {'pfrac': 1.0}, # weight posterior over evidence by 100%
    'nested_target_n_effective': 2000, # target effective sample size
    'nested_dlogz_init': 0.02,
    # FSPS info
    'zcontinuous': 2,
    'compute_vega_mags': False,
    'initial_disp':0.1,
    'interp_type': 'logarithmic',
    'nbins_sfh': 7,
    'df': 2,
    'agelims': [0.0,7.4772,8.0,8.5,9.0,9.5,9.8,10.0],
}

One thing to note here is that the `dynesty` settings listed above are far less stringent than those used in the paper. In the paper, we used `nested_nlive_init = 1000` and `nested_target_n_effective = 200000`. Downgrading the settings in the notebook here is just to speed up the fits by calling the emulator/FSPS fewer times - in real-world use, you'll want to use more stringent settings!

Now we can load the mock observation:

In [4]:
obs = load_obs(**run_params)

Next we can load the SPS object.

In [5]:
sps_emul = load_sps_emulator(**run_params)

Somewhat counterintuitively, we actually don't need this to be set to anything when using the emulator (all of the emulation stuff takes place in the model object). Hence:

In [ ]:
sps_emul

Speaking of the model object:

In [6]:
model_emul = load_model_emulator(obs=obs, sps=sps_emul, **run_params)

No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)


One thing we need to do when fitting with the emulator is taking the emulator's uncertainties in each filter into account - to do this, we'll use the `modify_obs` function provided by this repo.

In [7]:
obs_emul = modify_obs(obs=obs, model=model_emul)

With all that out of the way, we can now fit the mock object with the emulator. With the `dynesty` settings chosen above, this shouldn't take too long (~1 minute).

In [8]:
output_emul = fit_model(obs_emul, model_emul, sps_emul, **run_params)

iter: 2540 | batch: 0 | nc: 1 | ncall: 108995 | eff(%):  2.330 | logz: 1273.808 +/-  0.413 | dlogz:  0.000 >  0.020        


done dynesty (initial) in 69.18255281448364s
done dynesty (dynamic) in 1.9073486328125e-06s


Now let's take a look at the posterior. First we'll need to resample using the sample weights.

In [9]:
resampled_emul = sample_posterior(
    output_emul["sampling"][0]["samples"],
    weights = np.exp(output_emul["sampling"][0]["logwt"]-output_emul["sampling"][0]["logz"][-1]),
    nsample = 10_000,
)

Then we can create a corner plot:

In [10]:
plt_emul = corner.corner(
    resampled_emul,
    labels = parnames,
    quantiles = [0.16, 0.5, 0.84],
    show_titles = True,
    truths = obs["truth"],
)

## Fitting with FSPS

In [5]:
sps_fsps = load_sps_fsps(**run_params)

In [8]:
model_fsps = load_model_fsps(obs=obs, sps=sps_fsps, **run_params)

Now we can actually run the fit using FSPS. This will take *much* longer (~6 hours).

In [ ]:
output_fsps = fit_model(obs, model_fsps, sps_fsps, **run_params)

/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 353 | batch: 0 | nc: 83 | ncall: 3488 | eff(%):  9.838 | logz: 632.555 +/-  0.277 | dlogz: 556.174 >  0.020            /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 355 | batch: 0 | nc: 50 | ncall: 3589 | eff(%):  9.623 | logz: 638.125 +/-  0.277 | dlogz: 550.535 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: Run

iter: 389 | batch: 0 | nc: 50 | ncall: 5289 | eff(%):  7.218 | logz: 785.079 +/-  0.297 | dlogz: 405.351 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 391 | batch: 0 | nc: 50 | ncall: 5389 | eff(%):  7.123 | logz: 791.738 +/-  0.299 | dlogz: 399.285 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 393 | batch: 0 | nc: 50 | ncall: 5489 | eff(%):  7.032 | logz: 795.324 +/-  0.294 | dlogz: 394

iter: 425 | batch: 0 | nc: 50 | ncall: 7089 | eff(%):  5.912 | logz: 867.622 +/-  0.307 | dlogz: 331.015 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 427 | batch: 0 | nc: 50 | ncall: 7189 | eff(%):  5.858 | logz: 869.570 +/-  0.282 | dlogz: 317.981 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 429 | batch: 0 | nc: 50 | ncall: 7289 | eff(%):  5.806 | logz: 870.977 +/-  0.275 | dlogz: 316

iter: 461 | batch: 0 | nc: 50 | ncall: 8889 | eff(%):  5.128 | logz: 937.659 +/-  0.280 | dlogz: 334.187 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 463 | batch: 0 | nc: 50 | ncall: 8989 | eff(%):  5.094 | logz: 939.522 +/-  0.289 | dlogz: 332.906 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 465 | batch: 0 | nc: 50 | ncall: 9089 | eff(%):  5.060 | logz: 942.096 +/-  0.296 | dlogz: 330

iter: 497 | batch: 0 | nc: 50 | ncall: 10689 | eff(%):  4.607 | logz: 984.420 +/-  0.296 | dlogz: 287.675 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 499 | batch: 0 | nc: 50 | ncall: 10789 | eff(%):  4.583 | logz: 986.300 +/-  0.294 | dlogz: 285.584 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 501 | batch: 0 | nc: 50 | ncall: 10889 | eff(%):  4.559 | logz: 990.926 +/-  0.316 | dlogz: 

...

iter: 1001 | batch: 0 | nc: 50 | ncall: 35889 | eff(%):  2.781 | logz: 1237.148 +/-  0.345 | dlogz: 39.196 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1003 | batch: 0 | nc: 50 | ncall: 35989 | eff(%):  2.779 | logz: 1237.624 +/-  0.345 | dlogz: 38.565 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1005 | batch: 0 | nc: 50 | ncall: 36089 | eff(%):  2.777 | logz: 1238.006 +/-  0.345 | dlo

iter: 1037 | batch: 0 | nc: 50 | ncall: 37689 | eff(%):  2.744 | logz: 1243.580 +/-  0.348 | dlogz: 32.214 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1039 | batch: 0 | nc: 50 | ncall: 37789 | eff(%):  2.742 | logz: 1243.850 +/-  0.347 | dlogz: 31.898 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1041 | batch: 0 | nc: 50 | ncall: 37889 | eff(%):  2.740 | logz: 1244.096 +/-  0.346 | dlo

iter: 1073 | batch: 0 | nc: 50 | ncall: 39489 | eff(%):  2.710 | logz: 1248.076 +/-  0.344 | dlogz: 27.294 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1075 | batch: 0 | nc: 50 | ncall: 39589 | eff(%):  2.709 | logz: 1248.258 +/-  0.344 | dlogz: 27.098 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1077 | batch: 0 | nc: 50 | ncall: 39689 | eff(%):  2.707 | logz: 1248.481 +/-  0.344 | dlo

iter: 1109 | batch: 0 | nc: 50 | ncall: 41289 | eff(%):  2.679 | logz: 1251.828 +/-  0.348 | dlogz: 24.138 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1111 | batch: 0 | nc: 50 | ncall: 41389 | eff(%):  2.678 | logz: 1252.010 +/-  0.348 | dlogz: 23.933 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1113 | batch: 0 | nc: 50 | ncall: 41489 | eff(%):  2.676 | logz: 1252.187 +/-  0.348 | dlo

iter: 1145 | batch: 0 | nc: 50 | ncall: 43089 | eff(%):  2.651 | logz: 1255.136 +/-  0.351 | dlogz: 21.710 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1147 | batch: 0 | nc: 50 | ncall: 43189 | eff(%):  2.650 | logz: 1255.346 +/-  0.352 | dlogz: 21.487 >  0.020    /home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:105: RuntimeWarning: divide by zero encountered in divide
  Rsigma = ckms / sigma
/home/elijahmathews/.local/lib/python3.11/site-packages/prospect/utils/smoothing.py:106: RuntimeWarning: divide by zero encountered in scalar divide
  R = ckms / fwhm
iter: 1149 | batch: 0 | nc: 50 | ncall: 43289 | eff(%):  2.648 | logz: 1255.542 +/-  0.352 | dlo